In [2]:
import os
import pandas as pd
import numpy as np
#from wordcloud import WordCloud
from nltk.stem.snowball import SnowballStemmer
import nltk
from nltk.corpus import stopwords
#nltk.download('stopwords')
from sklearn.feature_extraction.text import CountVectorizer
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.decomposition import LatentDirichletAllocation as LDA
import warnings
import time
warnings.simplefilter("ignore", DeprecationWarning)
import matplotlib.pyplot as plt
import spacy
import de_core_news_sm
nlp = de_core_news_sm.load()

In [3]:
lemmatizing=True # with spacy; manually added words are definetly needed
stemming=False # lemmatizing is recommended instead
stopword_removal = False # didn't work as good as I expected

Create Dataframe with transcripts

In [4]:
"tagesschau_04012013_2000_.wav.txt".split("_")[1][0:2]

'04'

In [17]:
#os.chdir("test_transcripts")
#transcriptions = os.listdir()
#print("Transcriptions which are used now")
#print(transcriptions)
# use following line instead of the line after the folowing to use "tagesschau" only
#df = pd.DataFrame(index=[i for i in range(len(transcriptions)) if "tagessschau" in transcriptions[i]], columns=['transcriptionName','content','year','month','day'])
df = pd.DataFrame(columns=['transcriptionName','content','year','month','day'])
df = df.fillna(0)
for transcription in os.listdir("test_transcripts"):
    # use following line to use "tagesschau" only
    #if "tagesschau" in str(transcriptions[transcription]):
    if 1==1: #placeholder for above line
        with open("test_transcripts/{}".format(transcription), "r") as f:
            df.loc[transcription,'transcriptionName'] = str(transcription)
            df.loc[transcription,'content'] = f.read()
            date_string = str(transcription).split("_")[1]
            df.loc[transcription, 'year'] = date_string[4:]
            df.loc[transcription, 'month'] = date_string[2:4]
            df.loc[transcription, 'day'] = date_string[0:2]
df = df.reset_index(drop=True)

In [18]:
df

transcriptionName  \
0    tagesschau_04012013_2000_.wav.txt   
1    tagesschau_02042013_2000_.wav.txt   
2    tagesschau_27092013_2000_.txt.txt   
3    tagesschau_20112013_2000_.txt.txt   
4    tagesschau_12012013_2000_.wav.txt   
..                                 ...   
357  tagesschau_03102013_2000_.txt.txt   
358  tagesschau_08022013_2000_.wav.txt   
359  tagesschau_06102013_2000_.txt.txt   
360  tagesschau_05102013_2000_.txt.txt   
361  tagesschau_22072013_2000_.wav.txt   

                                               content  year month day  
0    hier ist das erste deutsche Fernsehen mit der ...  2013    01  04  
1    hier ist das erste deutsche Fernsehen mit der ...  2013    04  02  
2    hier ist das erste deutsche Fernsehen mit der ...  2013    09  27  
3    hier ist das erste deutsche Fernsehen mit der ...  2013    11  20  
4    hier ist das erste deutsche Fernsehen mit der ...  2013    01  12  
..                                                 ...   ...   ...  ..  
357  wie ist das erste deutsche Fernsehen mit der T...  2013    10  03  
358  hier ist das erste deutsche Fernsehen mit der ...  2013    02  08  
359  hier ist das erste deutsche Fernsehen mit der ...  2013    10  06  
360  hier ist das erste deutsche Fernsehen mit der ...  2013    10  05  
361  hier ist das erste deutsche Fernsehen mit der ...  2013    07  22  

[362 rows x 5 columns]

In [5]:
non_nouns=[] # init array for all non-nouns found by spacy

# preprocessing for topic modelling, in this case LDA (latent dirichlet analysis)
# remove "newline" and punctuation
df['content'] = df["content"].apply(lambda x: x.replace("\n","").replace(".",""))
# create token for spacy
doc = nlp(df.loc[transcript,'content'])
# lemmatize with help of spacy (maybe we can try another library for this)
df.loc[transcript,'content'] = ((",".join([x.lemma_ for x in doc])).replace(","," "))
doc = nlp(df.loc[transcript,'content'])
# write everything lowercase
df.loc[transcript,'content'] = df.loc[transcript,'content'].lower()
df.at[transcript,'content'] = df.loc[transcript,'content'].split()
    
    # stemming -> deprecated, use lemmatization instead
    if stemming:
        stemmer_tr=SnowballStemmer('german',ignore_stopwords=True)
        df.at[transcript,'content'] = [stemmer_tr.stem(word) for word in df.at[transcript,'content']]
        #print(df.at[i,'content'])
    
    # stopword removal
    if stopword_removal:
        stop_words=set(stopwords.words('german'))
        df.at[transcript,'content'] = [word for word in df.at[transcript,'content'] if word not in stop_words]
    
    # compensate structure for splitting
    df.at[transcript,'content'] = ','.join(df.loc[transcript,'content'])
    df.at[transcript,'content'] = (df.loc[transcript,'content']).replace(','," ")
    

non_nouns = [str(element) for element in non_nouns]

# remove all upper-case elements, not sure atm whether we need to do that
#non_nouns = [elem for elem in non_nouns if elem.lower()==elem]

# remove duplicates
non_nouns = (list(dict.fromkeys(non_nouns)))

# we need more words than spacy finds, I think LDA needs a lot of fine tuning
wordsToReplaceManually=['erst deutsch fernseh tagesschau','dame', 'herr','heut','ganz',
                'seit','jahr','neu','mehr','deutsch','schon','gross','wurd',
                'erst','imm','mal','gibt','sieht','klein','gut','etwa','ja',
                'beid','letzt','moglich','musst','klar','kommt','sagt','frag',
               'abend','lang','gest','morg','dabei','deshalb','einfach','schnell',
               'tag','zwei','wenig','beim','dafur','alt','drei','sag','kurz','ander',
                'dramatische','einig','eng','frischen','stillen','mensch','uhr','nacht',
                'land','norden','süden','woche','ende','heut']

# convert to matching format
for transcript in range(len(df)):
    df.at[transcript,'content'] = df.loc[transcript,'content'].split()
    
# remove non_nouns
#for i in range(len(df)):
#    removeFromWords = []
#    for j in df.loc[i,'content']:
#        if j in non_nouns:
#            removeFromWords.append(j)
#    removeFromWords = list(dict.fromkeys(removeFromWords))
#    df.at[i,'content'] = [word for word in df.loc[i,'content'] if word not in removeFromWords]
    
#remove manually chosen words
#for i in range(len(df)):
#    removeFromWords = []
#    for j in df.loc[i,'content']:
#        if j in wordsToReplaceManually:
#            removeFromWords.append(j)
#            #df.loc[i,'content'] = df.loc[i,'content'].replace(j.lower(),"")
#    #print(len(removeFromWords))
#    removeFromWords = list(dict.fromkeys(removeFromWords))
#    #print(len(removeFromWords))
#    df.at[i,'content'] = [word for word in df.loc[i,'content'] if word not in removeFromWords]

# convert to matching format
for transcript in range(len(df)):
    df.at[transcript,'content'] = ','.join(df.loc[transcript,'content'])
    df.at[transcript,'content'] = (df.loc[transcript,'content']).replace(','," ")

In [6]:
from gensim.models.phrases import Phrases, Phraser
sent = [row.split() for row in df['content']]
phrases = Phrases(sent, min_count=20, progress_per=10000)
bigram = Phraser(phrases)
sentences = bigram[sent]

In [7]:
sent

[['hier',
  'sein',
  'der',
  'erste',
  'deutsch',
  'fernsehen',
  'mit',
  'der',
  'tagesschau',
  'gut',
  'abend',
  'meinen',
  'dame',
  'und',
  'herr',
  'ich',
  'begrüßen',
  'ich',
  'zur',
  'tagesschau',
  'der',
  'frage',
  'wie',
  'atommüll',
  'entsorgen',
  'werden',
  'soll',
  'entfachen',
  'erneut',
  'diskussion',
  'umweltverbände',
  'befürchten',
  'hoch',
  'radioaktiv',
  'abfall',
  'aus',
  'deutschland',
  'können',
  'künftig',
  'ins',
  'ausland',
  'exportieren',
  'werden',
  'etwa',
  'nach',
  'russland',
  'können',
  'einen',
  'geplant',
  'gesetzesänderung',
  'ich',
  'soll',
  'einen',
  'entsorgung',
  'im',
  'ausland',
  'grundsätzlich',
  'ermöglichen',
  'der',
  'umweltministerium',
  'betonen',
  'mit',
  'der',
  'gesetz',
  'werden',
  'einen',
  'eu-vorgabe',
  'umsetzen',
  'zielen',
  'sein',
  'ich',
  'weit',
  'deutsch',
  'atommüll',
  'in',
  'deutschland',
  'zu',
  'entsorgen',
  'der',
  'ausstieg',
  'aus',
  'der',
 

In [8]:
import multiprocessing

from gensim.models import Word2Vec

In [9]:
cores = multiprocessing.cpu_count() # Count the number of cores in a computer
w2v_model = Word2Vec(min_count=10,
                     window=2,
                     #size=300,
                     sample=6e-5, 
                     alpha=0.03, 
                     min_alpha=0.0007, 
                     negative=20,
                     workers=cores-1)

In [10]:
w2v_model.build_vocab(sentences, progress_per=2000)

In [11]:
w2v_model.train(sentences, total_examples=w2v_model.corpus_count, epochs=30, report_delay=1)


(8247918, 21645000)

In [12]:
w2v_model.init_sims(replace=True)

In [49]:
w2v_model.wv.most_similar(positive=["china"])

[('japan', 0.7508368492126465),
 ('peking', 0.6546514630317688),
 ('usa', 0.6432200074195862),
 ('südkorea', 0.6402639746665955),
 ('beziehung', 0.6391863226890564),
 ('asien', 0.5902996063232422),
 ('russland', 0.5887837409973145),
 ('außerhalb', 0.5862942337989807),
 ('nordkoreanische', 0.5856480598449707),
 ('volksrepublik', 0.5790687203407288)]

In [45]:
w2v_model.wv.doesnt_match(["gysi", "lindner", "westerwelle"])

'westerwelle'